## Filtering a Data Observatory dataset using "Who's On First" in CARTOFrames

This notebook illustrates how to use the admin. region geometries from Who's on First (public data) to filter a dataset from CARTO's [Data Observatory](https://carto.com/spatial-data-catalog/) using [CARTOFrames](https://carto.com/cartoframes/) methods.

The notebook is organized as follows:
0. Setup account
1. Access a dataset from a Data Observatory subscription to be filtered
2. Who's on First for filtering data in cities

**Documentation**
- CARTO Spatial Data Catalogue - [link](https://carto.com/spatial-data-catalog/browser/)
- CARTOFrames technical documentation - [link](https://carto.com/developers/cartoframes/)
- "Who's on First" GeoJSON data product - [link](https://carto.com/spatial-data-catalog/browser/geography/wof_geojson_4e78587c/data)

### 0. Setup

In [1]:
import geopandas as gpd
import pandas as pd

from cartoframes.auth import set_default_credentials
from cartoframes.data.observatory import *
from cartoframes.viz import *

pd.set_option('display.max_columns', None)

In [2]:
set_default_credentials('creds.json')

### 1. Access a dataset from a Data Observatory subscription to be filtered

First, we check our data subscriptions from the Data Observatory to select which dataset we want to filter.

In [3]:
Catalog().subscriptions().datasets.to_dataframe()

slug  \
0         lg_parcels_ef7cdae4   
1     sg_social_dist_667d8e8e   
2    ine_sociodemogr_c8c87afe   
3   expn_sociodemogr_25b78bba   
4     mc_geographic__7980c5c3   
5    acs_sociodemogr_b758e778   
6    can_sociodemogr_affc7f83   
7      can_employment_e3bbbb6   
8      wp_population_cd347169   
9      wp_population_35d01fd4   
10     wp_population_6bf077c7   
11   spa_geosocial_s_d5dc42ae   
12   expn_consumer_se_7d6172d   
13  expn_sociodemogr_81aa1d1e   
14   cdb_spatial_fea_d23a5c97   
15   cdb_spatial_fea_802d4d44   
16   cdb_spatial_fea_7bd51aec   
17    ws_climatology_83bcb297   
18       uc_activity_ae564b62   
19    uc_home_and_wo_b42b8699   
20  expn_sociodemogr_8d3aa47a   
21       ws_forecast_39e1ab6a   
22       ws_historic_43f694cc   

                                                 name  \
0         Parcels - United States of America (Parcel)   
1   Social Distancing Metrics - United States of A...   
2          Sociodemographics (Spain, Census Sections)   
3            Sociodemographics - Thailand (Grid 250m)   
4   Geographic Insights - United States of America...   
5   Sociodemographics - United States of America (...   
6     Sociodemographics - Canada (Dissemination Area)   
7   Employment And Income - Canada (Dissemination ...   
8   Population Mosaics - Switzerland (Grid 1km, 2020)   
9      Population Mosaics - Belgium (Grid 100m, 2015)   
10        Population Mosaics - Italy (Grid 1km, 2020)   
11  Geosocial Segments - United States of America ...   
12             Consumer Segments - Russia (Grid 250m)   
13             Sociodemographics - Russia (Grid 250m)   
14             Spatial Features - Spain (Quadgrid 15)   
15            Spatial Features - France (Quadgrid 15)   
16            Spatial Features - Guyana (Quadgrid 15)   
17            Climatology - Japan (Grid 22km, hourly)   
18               Activity - Philippines (Quadgrid 17)   
19          Home And Work - Philippines (Quadgrid 17)   
20        Sociodemographics - Philippines (Grid 250m)   
21            Forecast - Spain (Municipality, hourly)   
22            Historic - Spain (Municipality, hourly)   

                                          description     category_id  \
0   Nationwide dataset with data from 140 million ...         housing   
1   Due to the COVID-19 pandemic, people are curre...         covid19   
2   Sociodemographic data from the Instituto Nacio...    demographics   
3   Worldview combines Experian's own datasets wit...    demographics   
4   Geographic Insights validate, evaluate and ben...       financial   
5   The American Community Survey (ACS) is an ongo...    demographics   
6   Sociodemographic data from Statistics Canada. ...    demographics   
7   Employment and income data from Statistics Can...    demographics   
8   Mosaiced 1km resolution global datasets. The m...    demographics   
9   Mosaiced 100m resolution global datasets. The ...    demographics   
10  Mosaiced 1km resolution global datasets. The m...    demographics   
11  By analysing feeds from Twitter, Instagram, Me...      behavioral   
12  WorldView segments has been developed to segme...    demographics   
13  Worldview combines Experian's own datasets wit...    demographics   
14  Spatial Features is a dataset curated by CARTO...         derived   
15  Spatial Features is a dataset curated by CARTO...         derived   
16  Spatial Features is a dataset curated by CARTO...         derived   
17  Global climatology data providing weather stat...   environmental   
18  Leveraging a global panel of location signals ...  human_mobility   
19  Paired with the Activity dataset, this data pr...  human_mobility   
20  Worldview combines Experian's own datasets wit...    demographics   
21                    10 and 15-day weather forecasts   environmental   
22    Past weather data from the year 2000 to present   environmental   

   country_id       data_source_id     provider_id  \
0         usa              parcels        landgrid   
1 

We identify the slug_id from the dataset we want to use. For example this one:

In [4]:
SpatialFeatures_esp_qk15 = Dataset.get('cdb_spatial_fea_d23a5c97')

In [5]:
SpatialFeatures_esp_qk15.to_dict()

{'slug': 'cdb_spatial_fea_d23a5c97',
 'name': 'Spatial Features - Spain (Quadgrid 15)',
 'description': 'Spatial Features is a dataset curated by CARTO providing access to a set of location-based features with global coverage that have been unified in common geographic supports (eg. Quadgrid). This product has been specially designed to facilitate spatial modeling at scale.\nSpatial Features includes core demographic data and POI aggregations by category that have been generated by processing and unifying globally available sources such as Worldpop and OpenStreetMap.\nThe current version of this product is available in two different spatial aggregations: Quadgrid level 15 (with cells of approximately 1x1km) and Quadgrid level 18 (with cells of approximately 100x100m).',
 'category_id': 'derived',
 'country_id': 'esp',
 'data_source_id': 'spatial_features',
 'provider_id': 'carto',
 'geography_name': 'Quadgrid 15 - Spain',
 'geography_description': 'Global Quadgrid (zoom level 15)',
 't

In [6]:
SpatialFeatures_esp_qk15.tail()

male            geoid        female  retail  leisure  tourism  \
0   3157.484307  031332122022031   3314.603374     202        2       30   
1   3100.709744  031333212123113   3112.707666     397        7       18   
2   5563.234994  031333330303331   5634.263423     267        5       33   
3   5752.487674  033121230020013   5897.919277     392        9       19   
4   4920.401140  033110331211321   5101.838268     386       12       24   
5  10488.067253  120222233002302  10980.102434     206        5       39   
6  10691.776215  120222233002303  11193.368209     144        6       44   
7   7046.002774  033111012101130   7718.364580     575       12       81   
8   4880.515167  033111230333220   5060.481569     234        5       60   
9   6940.973733  031333033310323   7317.757894     320       15       21   

   education  financial  food_drink  healthcare    population country_iso  \
0          3         20         217          17   6987.135426       Spain   
1         13         29         227          41   6213.417445       Spain   
2         10         32         230          39  11197.498466       Spain   
3         22         41         239          46  13530.062792       Spain   
4         11         17         240          38  10022.239175       Spain   
5          9         19         240          29  21468.169211       Spain   
6         13         30         240          40  21885.144834       Spain   
7         38         25         501          48  14764.367519       Spain   
8          4         17         247          15   9940.996620       Spain   
9          1         36         251          33  14258.731450       Spain   

   male_1_to_4  male_5_to_9  male_under_1  female_1_to_4  female_5_to_9  \
0   120.913153   163.556262     30.859980     112.445169     152.122509   
1   116.135321   156.329847     29.640561     107.896359     146.732161   
2   207.438940   282.454383     52.943473     196.299369     263.708241   
3   214.959833   292.499451     54.862983     205.108661     275.753969   
4   185.931533   251.828674     47.454258     175.431490     237.010205   
5   399.577618   543.086551    101.981938     374.481191     504.032327   
6   407.338614   553.634872    103.962726     381.754702     513.822090   
7   273.552370   370.482714     69.817227     258.793396     349.655445   
8   184.424333   249.787283     47.069582     174.009405     235.088947   
9   264.518769   357.406697     67.511636     249.595717     338.068831   

   male_10_to_14  male_15_to_19  male_20_to_24  male_25_to_29  male_30_to_34  \
0     179.977780     169.691305     162.016885     168.189652     180.966714   
1     171.439127     162.141215     156.255203     163.785669     177.375590   
2     310.187053     294.944600     277.136621     291.315402     318.226120   
3     323.571403     298.909093     289.252283     296.326437     318.596845   
4     277.479072     262.715527     251.839640     260.796087     279.359516   
5     597.000008     565.179574     533.200418     543.255342     585.150797   
6     608.595502     576.157012     543.556738     553.806953     596.516153   
7     408.169877     384.237815     361.315362     370.977625     400.892505   
8     275.229765     260.585895     249.798178     258.682006     277.094953   
9     394.396529     372.588657     354.263577     365.453562     393.743390   

   male_35_to_39  male_40_to_44  male_45_to_49  male_50_to_54  male_55_to_59  \
0     220.835550     269.261748     263.299398     248.028995     227.292451   
1     216.347498     264.268170     258.871424     245.878540     227.791271   
2     392.201611     481.832879     471.522448     446.028405     404.935209   
3     400.574748     495.122733     488.513948     459.693972     418.807097   
4     345.971107     422.165983     413.846829     389.538337     356.188780   
5     735.436253     911.480321     896.233391     834.498850     751.953428   
6     749.720600     929.183921     913.640858     850.7072

### 2. Who's On First GeoJSON for filtering data in cities

CARTO's Data Observatory also provides direct access to a group of public datasets. You can navigate and explore our Spatial Data Catalog from within your Python notebook with the Data Discovery methods in CARTOFrames or using our [Spatial Data Catalog](https://carto.com/spatial-data-catalog/browser/?license=public).

["Who's on First"](https://whosonfirst.org/) is a gazetteer (o big list) of places, each with a stable identifier and some number of descriptive properties about that location. 


We can use the WoF GeoJSON to find the city boundaries to use then for filtering the data from other datasets from the Data Observatory.

In [7]:
Catalog().provider('whos_on_first').public().geographies.to_dataframe()

slug                               name  \
0    wof_ancestors_eaaeac75                 Ancestors - Global   
1  wof_concordance_392f80ad              Concordances - Global   
2      wof_geojson_4e78587c                   GeoJSON - Global   
3        wof_names_5a30fa98                     Names - Global   
4          wof_spr_850ad7e9  Standard Places Response - Global   

                                         description country_id  \
0  A normalized view of the hierarchies in 'geojs...        glo   
1  Relationship between Who's On First identifier...        glo   
2  The main table in Who's On First. Holds all th...        glo   
3  What things are called in Who's On First. A no...        glo   
4  The "Standard Places Response" (or SPR) is an ...        glo   

     provider_id geom_type geom_coverage update_frequency  is_public_data  \
0  whos_on_first  MULTIPLE          None             None            True   
1  whos_on_first  MULTIPLE          None             None            True   
2  whos_on_first  MULTIPLE          None             None            True   
3  whos_on_first  MULTIPLE          None             None            True   
4  whos_on_first  MULTIPLE          None             None            True   

  lang   version   provider_name  \
0  eng  20190520  Who's On First   
1  eng  20190520  Who's On First   
2  eng  20190520  Who's On First   
3  eng  20190520  Who's On First   
4  eng  20190520  Who's On First   

                                                  id  
0  carto-do-public-data.whos_on_first.geography_g...  
1  carto-do-public-data.whos_on_first.geography_g...  
2  carto-do-public-data.whos_on_first.geography_g...  
3  carto-do-public-data.whos_on_first.geography_g...  
4  carto-do-public-data.whos_on_first.geography_g...

Note that the ID to access the WoF GeoJSON table is 'wof_geojson_4e78587c'.

In [8]:
wof_geojson = Geography.get('wof_geojson_4e78587c')

In [9]:
wof_geojson.to_dict()

{'slug': 'wof_geojson_4e78587c',
 'name': 'GeoJSON - Global',
 'description': "The main table in Who's On First. Holds all the relevant information for a place in the 'body' JSON field.",
 'country_id': 'glo',
 'provider_id': 'whos_on_first',
 'geom_type': 'MULTIPLE',
 'update_frequency': None,
 'is_public_data': True,
 'lang': 'eng',
 'version': '20190520',
 'provider_name': "Who's On First",
 'id': 'carto-do-public-data.whos_on_first.geography_glo_geojson_20190520'}

Now we are going to perform a query to the table in order to retrieve the different geometries given a city name and a country ISO Alpha-2 code. As we are looking for city boundaries, we can also limit our search to the placetype = 'locality' if we find that this is the specific type of place for our needs.

In [10]:
city_name = "'Madrid'"
country_code = "'ES'"
placetype = "'locality'"

sql_query = f"SELECT * FROM $geography$ WHERE name = {city_name} AND country = {country_code}"

wof_geojson_filtered = wof_geojson.to_dataframe(sql_query=sql_query)

wof_geojson_filtered

geoid         id                                               body  \
0   85682783   85682783  {"id": 85682783, "type": "Feature", "propertie...   
1  101748283  101748283  {"id": 101748283, "type": "Feature", "properti...   
2  404338863  404338863  {"id": 404338863, "type": "Feature", "properti...   

     name country  parent_id  is_current   placetype geometry_type  \
0  Madrid      ES  404227387           1      region  MultiPolygon   
1  Madrid      ES   85682783           1    locality  MultiPolygon   
2  Madrid      ES   85682783           0  localadmin       Polygon   

                                                bbox  \
0  POLYGON((-3.05298331 39.88471951, -3.05298331 ...   
1  POLYGON((-3.5180508952556 40.312064309035, -3....   
2  POLYGON((-3.51823494 40.31206394, -3.51823494 ...   

                                                geom  lastmodified  \
0  MULTIPOLYGON(((-4.31950989 40.64764365, -4.318...    1553814873   
1  POLYGON((-3.77455610356056 40.4003144849762, -...    1536881193   
2  POLYGON((-3.88557655 40.57445562, -3.88560442 ...    1513267506   

      lastmodified_timestamp  
0  2019-03-28 23:14:33+00:00  
1  2018-09-13 23:26:33+00:00  
2  2017-12-14 16:05:06+00:00

It may happen that we find that there are more than one locality with the same name. In order to select the right polygon, we can build a map with a category widget that will allow us to decide for the specific geometry that we are looking for.

In [17]:
wof_geojson_filtered['geoid_str'] = wof_geojson_filtered['geoid'].astype(str) 
Map(
    Layer(
      wof_geojson_filtered, # where the data comes from
      color_category_style('geoid_str',palette='Vivid',opacity=0.6,stroke_width=0.2),
      widgets=[category_widget('geoid_str','Select geoid to visualize')],
      popup_hover=[popup_element('geoid','geoid'),
                        popup_element('name','name'),
                        popup_element('placetype','placetype')],
      legends=color_category_legend('Geoid'),
      geom_col='geom', #the name of the column on the query that has a GEOGRAPHY data
      encode_data = False  
  )
)

Once we know which geometry (i.e. polygon of city boundaries) is the right one for our tests, we should copy/note its associated geoid.

As in this example we want to filter the data for Madrid, we will use geoid = '	101748283'.

In [12]:
"""Helper function for downloading only the data within the area (geometry) of interest
    Args:
        do_dataset: DO Dataset you'd like to download for a specific area of interest
        do_geom_dataset: DO Dataset containing the geometry you'd like to use as filter (your area of interest)
        target_geoid: geoid of the geometry you'd like to use as filter (your area of interest)
"""
def filter_data(do_dataset, do_geom_dataset, target_geoid):
    do_geom_dataset_id=do_geom_dataset.id
    sql_query = f"""WITH do_geom AS (
      SELECT geom
      FROM `{do_geom_dataset_id}`
      WHERE geoid = '{target_geoid}')

      SELECT do_d.* FROM $dataset$ do_d, do_geom WHERE ST_Intersects(do_d.geom, do_geom.geom)"""
    filtered_data = do_dataset.to_dataframe(sql_query = sql_query)
    return filtered_data

In [13]:
SpatialFeatures_esp_qk15_madrid = filter_data(SpatialFeatures_esp_qk15,wof_geojson,'101748283')
SpatialFeatures_esp_qk15_madrid.head()

geoid     do_date country_iso country_iso_a3   population  \
0  33111012100231  2020-01-01       Spain            ESP  2821.407676   
1  33111012112103  2020-01-01       Spain            ESP  4211.926348   
2  33111010333003  2020-01-01       Spain            ESP  2940.160426   
3  33111010323201  2020-01-01       Spain            ESP  1953.053871   
4  33111010302231  2020-01-01       Spain            ESP    26.484580   

        female         male  female_under_1  female_1_to_4  female_5_to_9  \
0  1474.946532  1346.461074       12.619821      49.454314      66.817661   
1  2201.867659  2010.058675       18.839446      73.827662      99.748466   
2  1537.026955  1403.133529       13.150988      51.535844      69.630015   
3  1020.997463   932.056375        8.735778      34.233599      46.252975   
4    13.845337    12.639243        0.118462       0.464228       0.627218   

   female_10_to_14  female_15_to_19  female_20_to_24  female_25_to_29  \
0        74.198982        69.822116        68.704864        74.128956   
1       110.767639       104.233648       102.565767       110.663101   
2        77.322015        72.760923        71.596650        77.249042   
3        51.362523        48.332735        47.559346        51.314049   
4         0.696507         0.655421         0.644933         0.695849   

   female_30_to_34  female_35_to_39  female_40_to_44  female_45_to_49  \
0        79.767044        96.886058       117.967211       117.709500   
1       119.079892       144.635941       176.106851       175.722126   
2        83.124433       100.963990       122.932445       122.663887   
3        55.216883        67.067124        81.660059        81.481666   
4         0.748774         0.909470         1.107359         1.104940   

   female_50_to_54  female_55_to_59  female_60_to_64  female_65_to_69  \
0       113.931398       106.953191        95.123228        80.496302   
1       170.081996       159.664616       142.004305       120.168563   
2       118.726763       111.454846        99.126961        83.884388   
3        78.866360        74.035860        65.846845        55.721696   
4         1.069475         1.003971         0.892923         0.755620   

   female_70_to_74  female_75_to_79  female_80_and_over  male_under_1  \
0        74.726742        61.961138          113.678006     13.341774   
1       111.555494        92.498418          169.703728     19.917212   
2        77.871984        64.569077          118.462706     13.903329   
3        51.727849        42.891157           78.690959      9.235533   
4         0.701461         0.581630            1.067097      0.125239   

   male_1_to_4  male_5_to_9  male_10_to_14  male_15_to_19  male_20_to_24  \
0    52.274691    70.797669      77.999520      73.426207      69.045821   
1    78.038052   105.689998     116.441251     109.613998     103.074766   
2    54.474931    73.777536      81.282515      76.516709      71.951957   
3    36.185940    49.008038      53.993354      50.827584      47.795366   
4     0.490703     0.664578       0.732182       0.689252       0.648134   

   male_25_to_29  male_30_to_34  male_35_to_39  male_40_to_44  male_45_to_49  \
0      70.892240      76.608848      94.859687     116.137476     113.934257   
1     105.831180     114.365187     141.610877     173.375340     170.086271   
2      73.876093      79.833307      98.852327     121.025696     118.729742   
3      49.073507      53.030693      65.664412      80.393471      78.868340   
4       0.665466       0.719128       0.890449       1.090184       1.069502   

   male_50_to_54  male_55_to_59  male_60_to_64  male_65_to_69  male_70_to_74  \
0     106.126800      95.711441      81.457317      67.209413      60.502372   
1     158.430937     142.882415     121.603210     100.333285      90.320708   
2     110.593669      99.739928      84.885847      70.038255      63.048912   
3      73.463809      66.254020      56.386934      46.524153      41.881360   
4       0.996213

In [18]:
Map(
    Layer(
      SpatialFeatures_esp_qk15_madrid, # where the data comes from
      color_continuous_style('population', palette=palettes.magenta,opacity=0.75,stroke_width=0.5),
      widgets=[formula_widget('population','sum','Total Population'),histogram_widget('population','Population by cell')],
      popup_hover=[popup_element('population','Population')],
      geom_col='geom', #the name of the column on the query that has a GEOGRAPHY data
      encode_data = False  
  )
)